In [1]:
import mechanize
import re
import pandas as pd
import numpy as np
from lxml import html 

In [2]:
CONSONANTS = [u'm̥', u'm', u'ɱ', u'n̼̊', u'n̼', u'n̥', u'n', u'ɳ̊', u'ɳ', u'ɲ̊', u'ɲ', 
              u'ŋ̊', u'ŋ', u'ɴ̥', u'ɴ', u'ʩ', u'ʩ̬', u'p', u'b', u'p̪', u'b̪', u't̼', u'd̼', 
              u't', u'd', u'ʈ', u'ɖ', u'c', u'ɟ', u'k', u'ɡ', u'q', u'ɢ', u'ʡ', u'ʔ', 
              u'ts', u'dz', u'tʃ', u'dʒ', u'ʈʂ', u'ɖʐ', u'tɕ', u'dʑ', u'pɸ', u'bβ', 
              u'p̪f', u'b̪v', u'tθ', u'dð', u'tθ̠', u'dð̠', u't̠ɹ̠̊˔', u'd̠ɹ̠˔', u'cç', u'ɟʝ', 
              u'kx', u'ɡɣ', u'qχ', u'ɢʁ', u'ʡħ', u'ʡʕ', u'ʔh', u's', u'z', u'ʃ', u'ʒ', 
              u'ʂ', u'ʐ', u'ɕ', u'ʑ', u'ɸ', u'β', u'f', u'v', u'θ̼', u'ð̼', u'θ', u'ð', u'θ̱', 
              u'ð̠', u'ɹ̠̊˔', u'ɹ̠˔', u'ç', u'ʝ', u'x', u'ɣ', u'χ', u'ʁ', u'ħ', u'ʕ', u'h', 
              u'ɦ', u'ʔ̞', u'ʋ̥', u'ʋ', u'ɹ̥', u'ɹ', u'ɻ̊', u'ɻ', u'j̊', u'j', u'ɰ̊', u'ɰ', u'ⱱ̟', 
              u'ⱱ', u'ɾ̼', u'ɾ̥', u'ɾ', u'ɽ̊', u'ɽ', u'ɢ̆', u'ʡ̮', u'ʙ', u'ʙ̪', u'r̼', u'r̥', u'r', 
              u'ɽr̥', u'ɽr', u'ʀ̥', u'ʀ', u'ʜ', u'ʢ', u'tɬ', u'dɮ', u'ʈɭ̊˔', u'cʎ̥˔', u'kʟ̝̊', 
              u'ɡʟ̝', u'ɬ', u'ɮ', u'ɭ̊˔', u'ɭ˔', u'ʎ̥˔', u'ʎ̝', u'ʟ̝̊', u'ʟ̝', u'l̼', u'l̥', u'l', 
              u'ɭ̊', u'ɭ', u'ʎ̥', u'ʎ', u'ʟ̥', u'ʟ', u'ʟ̠', u'ɺ̼', u'ɺ', u'ɭ̆', u'ʎ̮', u'ʟ̆', u'ʘ', 
              u'ʘ̬', u'ʘ̃', u'ǀ', u'ǀ̬', u'ǀ̃', u'ǃ', u'ǃ̬', u'ǃ̃', u'ǂ', u'ǂ̬', u'ǂ̃', u'ǁ', u'ǁ̬', 
              u'ǁ̃', u'ǃ˞', u'ǃ̬˞', u'ǃ̃˞', u'ʘ̃ˀ', u'ʘˀ', u'ˀʘ̃', u'ʘ͡q', u'ʘ͡qχ', u'ʘ͡qʼ', u'ʘ͡qχʼ', 
              u'¡', u'ʞ', u'ɓ', u'ɗ', u'ᶑ', u'ʄ', u'ɠ', u'ʛ', u'ɓ̥', u'ɗ̥', u'ᶑ̥', u'ʄ̊', u'ɠ̊', u'ʛ̥', 
              u'pʼ', u'tʼ', u'ʈʼ', u'cʼ', u'kʼ', u'qʼ', u'ʡʼ', u'ɸʼ', u'fʼ', u'θʼ', u'sʼ', u'ɬʼ', 
              u'ʃʼ', u'ʂʼ', u'ɕʼ', u'çʼ', u'xʼ', u'χʼ', u'tθʼ', u'tsʼ', u'tɬʼ', u'tʃʼ', u'ʈʂʼ', 
              u'tɕʼ', u'cçʼ', u'cʎ̝̥ʼ', u'kxʼ', u'kʟ̝̊ʼ', u'qχʼ', u'ʍ', u'w', u'ɥ̊', u'ɥ', u'ɫ', u'k͡p', 
              u'ɡ͡b', u'ŋ͡m', u'ɧ', u't͡p', u'd͡b', u'n͡m', u'q͡ʡ']

In [3]:
LOGIN_URL = "http://conworkshop.info/login_standard.php"
CONLANGS_URL = "http://conworkshop.info/conlangs.php"

VOWELS = [u'i', u'y', u'ɨ', u'ʉ', u'ɯ', u'u', u'ɪ', u'ʏ', u'ɪ̈', u'ʊ̈', u'ɯ̽', u'ʊ', u'e', u'ø', u'ɘ',
          u'ɵ', u'ɤ', u'o', u'ə', u'ɛ', u'œ', u'ɜ', u'ɞ', u'ʌ', u'ɔ', u'æ', u'ɐ', u'a', u'ɶ', u'ɑ', u'ɒ']
'''CONSONANTS = [u'm', u'ɱ', u'n̪', u'n', u'ɳ', u'ɲ', u'ŋ', u'ɴ', u'p', u'b', u'p̪', u'b̪', u't̪', 
              u'd̪', u't', u'd', u'ʈ', u'ɖ', u'c', u'ɟ', u'k', u'ɡ', u'q', u'ɢ', u'ʡ', u'ʔ', 
              u'ɸ', u'β', u'f', u'v', u'θ', u'ð', u's', u'z', u'ʃ', u'ʒ', u'ʂ', u'ʐ', u'ç', 
              u'ʝ', u'x', u'ɣ', u'χ', u'ʁ', u'ħ', u'ʕ', u'h', u'ɦ', u'ʋ', u'ɹ', u'ɻ', u'j', 
              u'ɰ', u'ʙ', u'r', u'ɽ͡r', u'ʀ', u'ʜ', u'ʢ', u'ⱱ̟', u'ⱱ', u'ɾ', u'ɽ', u'ɢ̆', u'ʡ̯', 
              u'ɬ', u'ɮ', u'ɭ˔̊', u'ʎ̥˔', u'ʟ̝̊', u'l', u'ɭ', u'ʎ', u'ʟ', u'ɺ', u'ɺ̢', u'ʎ̯']'''

"CONSONANTS = [u'm', u'\xc9\xb1', u'n\xcc\xaa', u'n', u'\xc9\xb3', u'\xc9\xb2', u'\xc5\x8b', u'\xc9\xb4', u'p', u'b', u'p\xcc\xaa', u'b\xcc\xaa', u't\xcc\xaa', \n              u'd\xcc\xaa', u't', u'd', u'\xca\x88', u'\xc9\x96', u'c', u'\xc9\x9f', u'k', u'\xc9\xa1', u'q', u'\xc9\xa2', u'\xca\xa1', u'\xca\x94', \n              u'\xc9\xb8', u'\xce\xb2', u'f', u'v', u'\xce\xb8', u'\xc3\xb0', u's', u'z', u'\xca\x83', u'\xca\x92', u'\xca\x82', u'\xca\x90', u'\xc3\xa7', \n              u'\xca\x9d', u'x', u'\xc9\xa3', u'\xcf\x87', u'\xca\x81', u'\xc4\xa7', u'\xca\x95', u'h', u'\xc9\xa6', u'\xca\x8b', u'\xc9\xb9', u'\xc9\xbb', u'j', \n              u'\xc9\xb0', u'\xca\x99', u'r', u'\xc9\xbd\xcd\xa1r', u'\xca\x80', u'\xca\x9c', u'\xca\xa2', u'\xe2\xb1\xb1\xcc\x9f', u'\xe2\xb1\xb1', u'\xc9\xbe', u'\xc9\xbd', u'\xc9\xa2\xcc\x86', u'\xca\xa1\xcc\xaf', \n              u'\xc9\xac', u'\xc9\xae', u'\xc9\xad\xcb\x94\xcc\x8a', u'\xca\x8e\xcc\xa5\xcb\x94', u'\xca\x9f\xcc\x9d\xcc\x8a', u'l', u'\xc9\xad', u

### Поиск форм на странице авторизации

In [4]:
br = mechanize.Browser()
br.open(LOGIN_URL)
for form in br.forms():
    print form

<login_form post http://conworkshop.info/login_standard.php application/x-www-form-urlencoded
  <HiddenControl(action=login_auth) (readonly)>
  <TextControl(email=)>
  <PasswordControl(s_pword=)>>


### Заполнение формы авторизации 

In [5]:
br.open(LOGIN_URL)
br.select_form( 'login_form' )
br.form[ 'email' ] = 'nhfancy@mail.ru'
br.form[ 's_pword' ] = '41601811'
br.submit()

<response_seek_wrapper at 0x118b3e290 whose wrapped object = <closeable_response at 0x118b6fdd0 whose fp = <socket._fileobject object at 0x118ad4e50>>>

### Переход на страницу со списком конлангов

In [6]:
response = br.open(CONLANGS_URL)
text = response.read()

In [7]:
url_conlang_name = re.findall(r"view_language.php...(\w+)\W",text)
for i in range(len(url_conlang_name)):
    url_conlang_name[i] = 'view_language.php?l=' + url_conlang_name[i] 
    
url_author_name = re.findall(r"view_profile.php.m.(\w+)\W",text)
for i in range(len(url_conlang_name)):
    url_author_name[i] = 'view_profile.php?m=' + url_author_name[i] 
    
Type = re.findall(r"ass..ls_...(\w+)\W",text)
#Status = span class="ls_2">Progressing</span></span><span>A priori</span></div><div class=\'list report\'

### Парсим профили конлангеров, запоминаем язык native с 5-ю звездами

In [8]:
uniq_authors = np.unique(np.array(url_author_name))
uniq_authors = uniq_authors[1:] # первый адрес битый TODO исправить
languages = list()
names = list()
for i, url in enumerate(uniq_authors):
    response = br.open("http://conworkshop.info/" + url)
    text = response.read()
    language = re.findall(r"nat_lang.php.n=..'>(\w+[^<]+)</a></span><span style='width: 24%;'>\
<b>native</b></span><span style='width: 25%;.>&#9733;&#9733;&#9733;&#9733;&#9733;", text)
    name = re.findall(r"class=\'mem\' style=\'color: #...... !important; \'>(\w+[^<]+)", text)
    names.append(name)
    languages.append(language)
    print language, name, i

['English'] ['Chad Buxton'] 0
[] ['Miguel Meana'] 1
['English'] ['Vulcanman'] 2
['English'] ['Alex Leonard'] 3
[] ['Shea Ruch'] 4
[] ['Manolo M\xc3\xbcller'] 5
[] ['Luis Felipe De La Maza Guajardo'] 6
[] ['Matty Beales'] 7
['English'] ['Andy Ayres'] 8
['Dutch (Nederlands)'] ['Thomas de Roo'] 9
['English'] ['Daly Barron'] 10
['Swedish (Svenska)'] ['Viktor Stamyr'] 11
['Portuguese (Portugu\xc3\xaas)'] ['Mayara Barros'] 12
['Icelandic (\xc3\x8dslenska)'] ['rafeind'] 13
['English'] ['Noah Hradek'] 14
[] [] 15
[] [] 16
[] [] 17
[] [] 18
[] [] 19
[] [] 20
[] [] 21
[] [] 22
['English'] ['Yonah Sienna'] 23
[] [] 24
['English', 'Spanish (Espa\xc3\xb1ol)'] ['Eli MCZ'] 25
['English'] ['Layne Trout'] 26
['Portuguese (Portugu\xc3\xaas)'] ['Loglorn'] 27
[] ['Thomas Batchelor'] 28
[] ['Skye Koons'] 29
[] ['Mark Amad\xc3\xa1n \xc3\x93 Domhnaill'] 30
['English'] ['Herman Miller'] 31
['Tagalog'] ['Bautista Rairai'] 32
['English'] ['Aargle Zymurgy'] 33
[] ['Sean Hawkins'] 34
['Spanish (Espa\xc3\xb1ol)'] 

In [43]:
language_info = pd.DataFrame(data = np.asarray([languages, names]).T.tolist(), columns = ['language', 'name'])

In [44]:
language_info.head()

language            name
0  [English]   [Chad Buxton]
1         []  [Miguel Meana]
2  [English]     [Vulcanman]
3  [English]  [Alex Leonard]
4         []     [Shea Ruch]

### Парсим языки

In [11]:
len(url_conlang_name)

5357

In [14]:
conlang_name = list()
conlang_type = list()
conlang_status = list()
conlang_phonems = list()
author_name = list()
for j, url in enumerate(url_conlang_name):
    try:
        response = br.open("http://conworkshop.info/" + url)
        text = response.read()

        author = re.findall(r"class=\'mem\' style=\'color: #...... !important; \'>(\w+[^<]+)", text)
        name = re.findall(r"<div class=\'title\'>([^<]+)</div>", text)
        typ = re.findall(r"Language type\r\n\t\t\t\t\t<span class=\'faux\'>([^<]+)</span>", text)
        status = re.findall(r"<span class=\"ls_.\">(\w+)</span>", text)

        parsed_body = html.fromstring(text)
        span  = parsed_body.xpath('//span[@class = "faux"]/text()')
        td = parsed_body.xpath('//td/text()')

        for i in range(0,len(td)):
            td[i] = unicode(td[i])
            if (td[i][0] == '[') or (td[i][0] == '('):
                td[i] = td[i][1:-1]

        consonants_vector = np.zeros(len(CONSONANTS))
        for i, consonants in enumerate(CONSONANTS):
            if consonants in td:
                consonants_vector[i] = 1
                td.remove(consonants)

        for i in range(0,len(td)):
            if u'\u2003' in td[i]:
                td[i] = td[i][0]

        for i, consonants in enumerate(CONSONANTS):
            if consonants in td:
                consonants_vector[i] = 1

        vowels_vector = np.zeros(len(VOWELS))
        for i, vowel in enumerate(VOWELS):
            if vowel in td:
                vowels_vector[i] = 1
        vector = list()
        for vowel in vowels_vector:
            vector.append(vowel)
        for consonant in consonants_vector:
            vector.append(consonant)

        conlang_phonems.append(vector)
        conlang_name.append(name)
        conlang_status.append(status)
        conlang_type.append(typ)
        author_name.append(author)
        print j
        print vector
        print author, name, status, typ
    except:
        print j
        print 'error'

0
[1.0, 0.0, 0.0, 0.0, 0.0, 1.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.

In [41]:
conlangs = pd.DataFrame(data = np.asarray([conlang_name, conlang_type, conlang_status, conlang_phonems, 
                        author_name]).T.tolist(),
                       columns = ['conlang_name', 'conlang_type', 'conlang_status', 'conlang_phonems', 'name'])

In [42]:
conlangs.head()

conlang_name  \
0  [Tirina [TNA], Sound samples in Tirina, Langua...   
1          [ Fuzzitan [UOE], Phonology, Orthography]   
2        [&apos;DraUz [DRZ], Phonology, Orthography]   
3          [&apos;Nga [RNI], Phonology, Orthography]   
4  [(Desert) Elvish [EL2], Language family relati...   

                    conlang_type conlang_status  \
0                     [A priori]   [Functional]   
1                [Proto-Conlang]          [New]   
2  [Artistic Language (Artlang)]          [New]   
3                     [A priori]          [New]   
4                     [A priori]   [Functional]   

                                     conlang_phonems           name  
0  [1.0, 0.0, 0.0, 0.0, 0.0, 1.0, 1.0, 0.0, 0.0, ...  [alynnidalar]  
1  [1.0, 1.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, ...  [Majicturtol]  
2  [1.0, 0.0, 0.0, 0.0, 0.0, 1.0, 1.0, 0.0, 0.0, ...       [Dolfyn]  
3  [1.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, ...      [Orikrin]  
4  [1.0, 0.0, 0.0, 0.0, 0.0, 1.0, 1.0, 0.0, 0.0, ...      [Cestion]

In [18]:
conlangs.to_csv('conlangs.csv', index=False)

In [22]:
conlangs

conlang_name  \
0     [Tirina [TNA], Sound samples in Tirina, Langua...   
1             [ Fuzzitan [UOE], Phonology, Orthography]   
2           [&apos;DraUz [DRZ], Phonology, Orthography]   
3             [&apos;Nga [RNI], Phonology, Orthography]   
4     [(Desert) Elvish [EL2], Language family relati...   
5     [(Gendered) Equestrian [GEQ], Phonology, Ortho...   
6     [(no name yet) [A12], Language family relation...   
7            [(None Yet) [OAE], Phonology, Orthography]   
8       [(Not Named Yet) [GL1], Phonology, Orthography]   
9     [(Sor-Sar) [ZOR], Language family relationship...   
10    [(TBD) [NNL], Language family relationships, P...   
11                             [*TBN* [TCR], Phonology]   
12                   [-- [EAE], Phonology, Orthography]   
13                                           [-- [FJU]]   
14                   [-- [SYR], Phonology, Orthography]   
15                                           [-- [YTE]]   
16                  [--- [INO], Phonology, Orthography]   
17                        [3/4 Dragon [TFD], Phonology]   
18           [9 Phonemes [NPQ], Phonology, Orthography]   
19                                [=e [PRR], Phonology]   
20                                 [? [ABE], Phonology]   
21                  [??? [NUH], Phonology, Orthography]   
22                [A Lar [ALR], Phonology, Orthography]   
23           [A&apos;ani [ANI], Phonology, Orthography]   
24               [Aaaaaa [AAA], Phonology, Orthography]   
25             [Aaawèèèj [AAE], Phonology, Orthography]   
26                                       [Aadagg [XZQ]]   
27    [Aalvunian Luwkeean [LGH], Phonology, Orthogra...   
28    [Aaric [AIS], Language family relationships, P...   
29             [Aarvesan [AAR], Phonology, Orthography]   
...                                                 ...   
5315  [Zuryuttic [ZRY], Language family relationship...   
5316              [Zutan [ZUT], Phonology, Orthography]   
5317          [Zuthuinin [ZTH], Phonology, Orthography]   
5318  [Zuvran [BUG], Language family relationships, ...   
5319  [Zveahe [XNA], Sound samples in Zveahe, Phonol...   
5320  [Zxy [ZXY], Language family relationships, Pho...   
5321      [Zyem Language [NDZ], Phonology, Orthography]   
5322  [zygiligleth [103], Sound samples in zygiligle...   
5323  [Zygiligleth Sign Language [ZSL], Language fam...   
5324             [Zyolra [ZYO], Phonology, Orthography]   
5325  [[Cornish/Breton Inspired] [BK1], Phonology, O...   
5326    [[Wendish-based] [WND], Phonology, Orthography]   
5327             [Łireti [LIR], Phonology, Orthography]   
5328                    [Ŋtha&apos;la [NTA], Phonology]   
5329         [Śraawateno [OEA], Phonology, Orthography]   
5330            [Śukepiu [SPU], Phonology, Orthography]   
5331           [Šarradin [E02], Phonology, Orthography]   
5332                                     [Ševkia [LDS]]   
5333  [Šigǆoha [SIZ], Language family relationships,...   
5334               [Šila [SLA], Phonology, Orthography]   
5335            [Żywośje [EGP], Phonology, Orthography]   
5336  [Žak [ZAK], Language family relationships, Pho...   
5337             [Žêcýya [ZEC], Phonology, Orthography]   
5338  [Žilèði [ZHI], Sound samples in Žilèði, Phonol...   
5339  [Ɔ Ñi [ONY], Language family relationships, Ph...   
5340  [Ćɛ&apos;ŋ sí Kătya [CEN], Phonology, Orthogra...   
5341  [Čëcen Mangap [CCM], Sound samples in Čëcen Ma...   
5342             [Čihken [ZIR], Phonology, Orthography]   
5343  [Ďomün [DMN], Language family relationships, P...   
5344                 [Ɣu [GHU], Phonology, Orthography]   

                                  conlang_type conlang_status  \
0                                   [A priori]   [Functional]   
1                              [Proto-Conlang]          [New]   
2                [Artistic Language (Artlang)]          [New]   
3                                   [A priori]          [New]   
4                                   [A priori]   [Functiona

In [49]:
language_info

language  \
0                                          [English]   
1                                                 []   
2                                          [English]   
3                                          [English]   
4                                                 []   
5                                                 []   
6                                                 []   
7                                                 []   
8                                          [English]   
9                               [Dutch (Nederlands)]   
10                                         [English]   
11                               [Swedish (Svenska)]   
12                          [Portuguese (Português)]   
13                            [Icelandic (Íslenska)]   
14                                         [English]   
15                                                []   
16                                                []   
17                                                []   
18                                                []   
19                                                []   
20                                                []   
21                                                []   
22                                                []   
23                                         [English]   
24                                                []   
25                      [English, Spanish (Español)]   
26                                         [English]   
27                          [Portuguese (Português)]   
28                                                []   
29                                                []   
...                                              ...   
2099                                              []   
2100                                              []   
2101                                       [English]   
2102                                       [English]   
2103                                       [English]   
2104                                       [English]   
2105  [Croatian (Hrvatski), Slovenian (Slovenščina)]   
2106                                       [English]   
2107                                       [English]   
2108                                       [English]   
2109                                       [English]   
2110                                              []   
2111                                              []   
2112                                       [English]   
2113                                       [English]   
2114                                       [English]   
2115                                              []   
2116                                              []   
2117                                              []   
2118                                       [English]   
2119                                       [English]   
2120                                              []   
2121                   [English, Hungarian (Magyar)]   
2122                                              []   
2123                                       [English]   
2124                                              []   
2125                                       [English]   
2126                                       [English]   
2127                                              []   
2128                                       [English]   

                                     name  
0                         ['Chad Buxton']  
1                        ['Miguel Meana']  
2                           ['Vulcanman']  
3                        ['Alex Leonard']  
4                           ['Shea Ruch']  
5                ['Manolo M\xc3\xbcller']  
6     ['Luis Felipe De La Maza Guajardo']  
7                        ['Matty Beales']  
8                          ['Andy Ayres']  
9                       ['Thomas de Roo']  
10                        ['Daly Barron']  
11                      ['Viktor Stamyr']  

In [46]:
for i in range(0,len(conlangs)):
    conlangs.name.loc[i] = str(conlangs.name.loc[i])
for i in range(0,len(language_info)):
    language_info.name.loc[i] = str(language_info.name.loc[i])

In [47]:
conlangs

conlang_name  \
0     [Tirina [TNA], Sound samples in Tirina, Langua...   
1             [ Fuzzitan [UOE], Phonology, Orthography]   
2           [&apos;DraUz [DRZ], Phonology, Orthography]   
3             [&apos;Nga [RNI], Phonology, Orthography]   
4     [(Desert) Elvish [EL2], Language family relati...   
5     [(Gendered) Equestrian [GEQ], Phonology, Ortho...   
6     [(no name yet) [A12], Language family relation...   
7            [(None Yet) [OAE], Phonology, Orthography]   
8       [(Not Named Yet) [GL1], Phonology, Orthography]   
9     [(Sor-Sar) [ZOR], Language family relationship...   
10    [(TBD) [NNL], Language family relationships, P...   
11                             [*TBN* [TCR], Phonology]   
12                   [-- [EAE], Phonology, Orthography]   
13                                           [-- [FJU]]   
14                   [-- [SYR], Phonology, Orthography]   
15                                           [-- [YTE]]   
16                  [--- [INO], Phonology, Orthography]   
17                        [3/4 Dragon [TFD], Phonology]   
18           [9 Phonemes [NPQ], Phonology, Orthography]   
19                                [=e [PRR], Phonology]   
20                                 [? [ABE], Phonology]   
21                  [??? [NUH], Phonology, Orthography]   
22                [A Lar [ALR], Phonology, Orthography]   
23           [A&apos;ani [ANI], Phonology, Orthography]   
24               [Aaaaaa [AAA], Phonology, Orthography]   
25             [Aaawèèèj [AAE], Phonology, Orthography]   
26                                       [Aadagg [XZQ]]   
27    [Aalvunian Luwkeean [LGH], Phonology, Orthogra...   
28    [Aaric [AIS], Language family relationships, P...   
29             [Aarvesan [AAR], Phonology, Orthography]   
...                                                 ...   
5315  [Zuryuttic [ZRY], Language family relationship...   
5316              [Zutan [ZUT], Phonology, Orthography]   
5317          [Zuthuinin [ZTH], Phonology, Orthography]   
5318  [Zuvran [BUG], Language family relationships, ...   
5319  [Zveahe [XNA], Sound samples in Zveahe, Phonol...   
5320  [Zxy [ZXY], Language family relationships, Pho...   
5321      [Zyem Language [NDZ], Phonology, Orthography]   
5322  [zygiligleth [103], Sound samples in zygiligle...   
5323  [Zygiligleth Sign Language [ZSL], Language fam...   
5324             [Zyolra [ZYO], Phonology, Orthography]   
5325  [[Cornish/Breton Inspired] [BK1], Phonology, O...   
5326    [[Wendish-based] [WND], Phonology, Orthography]   
5327             [Łireti [LIR], Phonology, Orthography]   
5328                    [Ŋtha&apos;la [NTA], Phonology]   
5329         [Śraawateno [OEA], Phonology, Orthography]   
5330            [Śukepiu [SPU], Phonology, Orthography]   
5331           [Šarradin [E02], Phonology, Orthography]   
5332                                     [Ševkia [LDS]]   
5333  [Šigǆoha [SIZ], Language family relationships,...   
5334               [Šila [SLA], Phonology, Orthography]   
5335            [Żywośje [EGP], Phonology, Orthography]   
5336  [Žak [ZAK], Language family relationships, Pho...   
5337             [Žêcýya [ZEC], Phonology, Orthography]   
5338  [Žilèði [ZHI], Sound samples in Žilèði, Phonol...   
5339  [Ɔ Ñi [ONY], Language family relationships, Ph...   
5340  [Ćɛ&apos;ŋ sí Kătya [CEN], Phonology, Orthogra...   
5341  [Čëcen Mangap [CCM], Sound samples in Čëcen Ma...   
5342             [Čihken [ZIR], Phonology, Orthography]   
5343  [Ďomün [DMN], Language family relationships, P...   
5344                 [Ɣu [GHU], Phonology, Orthography]   

                                  conlang_type conlang_status  \
0                                   [A priori]   [Functional]   
1                              [Proto-Conlang]          [New]   
2                [Artistic Language (Artlang)]          [New]   
3                                   [A priori]          [New]   
4                                   [A priori]   [Functiona

In [68]:
data = pd.merge(conlangs, language_info, how = 'left',  on = 'name')
for i in range(0,len(data)):
    data.language.loc[i] = str(data.language.loc[i])
data = data[data.language != '[]']
data = data[data.name != '[]']
data.index = range(0,len(data))

In [70]:
data

conlang_name  \
0     [Tirina [TNA], Sound samples in Tirina, Langua...   
1           [&apos;DraUz [DRZ], Phonology, Orthography]   
2             [&apos;Nga [RNI], Phonology, Orthography]   
3     [(Desert) Elvish [EL2], Language family relati...   
4     [(no name yet) [A12], Language family relation...   
5            [(None Yet) [OAE], Phonology, Orthography]   
6     [(Sor-Sar) [ZOR], Language family relationship...   
7     [(TBD) [NNL], Language family relationships, P...   
8                              [*TBN* [TCR], Phonology]   
9                                            [-- [YTE]]   
10                                [=e [PRR], Phonology]   
11                  [??? [NUH], Phonology, Orthography]   
12           [A&apos;ani [ANI], Phonology, Orthography]   
13               [Aaaaaa [AAA], Phonology, Orthography]   
14             [Aaawèèèj [AAE], Phonology, Orthography]   
15    [Aalvunian Luwkeean [LGH], Phonology, Orthogra...   
16    [Aaric [AIS], Language family relationships, P...   
17    [Aastoyakap [QAA], Language family relationshi...   
18                  [Aán [AOA], Phonology, Orthography]   
19    [Abea [ABB], Language family relationships, Ph...   
20                                        [Abern [ABR]]   
21                [Abnar [ABN], Phonology, Orthography]   
22              [Abouven [ABV], Phonology, Orthography]   
23                [Abtec [APT], Phonology, Orthography]   
24              [Abyssal [ABY], Phonology, Orthography]   
25                          [Abyssian [AYS], Phonology]   
26    [Acadian [ACD], Language family relationships,...   
27    [Achiyitqan [ACY], Sound samples in Achiyitqan...   
28             [Acorithe [ACO], Phonology, Orthography]   
29    [Adenish [WMN], Sound samples in Adenish, Lang...   
...                                                 ...   
4078                          [Zortro [ZRT], Phonology]   
4079  [Zose [ZSE], Language family relationships, Ph...   
4080  [Zosla [PZS], Language family relationships, P...   
4081  [Zostine [ZOS], Language family relationships,...   
4082             [Zucini [AVZ], Phonology, Orthography]   
4083            [Zuk'ana [ZKA], Phonology, Orthography]   
4084  [Zuryuttic [ZRY], Language family relationship...   
4085  [Zxy [ZXY], Language family relationships, Pho...   
4086  [zygiligleth [103], Sound samples in zygiligle...   
4087  [Zygiligleth Sign Language [ZSL], Language fam...   
4088             [Zyolra [ZYO], Phonology, Orthography]   
4089  [[Cornish/Breton Inspired] [BK1], Phonology, O...   
4090    [[Wendish-based] [WND], Phonology, Orthography]   
4091             [Łireti [LIR], Phonology, Orthography]   
4092                    [Ŋtha&apos;la [NTA], Phonology]   
4093            [Śukepiu [SPU], Phonology, Orthography]   
4094           [Šarradin [E02], Phonology, Orthography]   
4095                                     [Ševkia [LDS]]   
4096  [Šigǆoha [SIZ], Language family relationships,...   
4097               [Šila [SLA], Phonology, Orthography]   
4098            [Żywośje [EGP], Phonology, Orthography]   
4099  [Žak [ZAK], Language family relationships, Pho...   
4100             [Žêcýya [ZEC], Phonology, Orthography]   
4101  [Žilèði [ZHI], Sound samples in Žilèði, Phonol...   
4102  [Ɔ Ñi [ONY], Language family relationships, Ph...   
4103  [Ćɛ&apos;ŋ sí Kătya [CEN], Phonology, Orthogra...   
4104  [Čëcen Mangap [CCM], Sound samples in Čëcen Ma...   
4105             [Čihken [ZIR], Phonology, Orthography]   
4106  [Ďomün [DMN], Language family relationships, P...   
4107                 [Ɣu [GHU], Phonology, Orthography]   

                         conlang_type conlang_status  \
0                          [A priori]   [Functional]   
1       [Artistic Language (Artlang)]          [New]   
2                          [A priori]          [New]   
3                          [A priori]   [Functional]   
4                          [A priori]          [New]   
5                          [A priori]           

In [71]:
data.to_csv('dataset_conlang.csv', index=False)